# Booj Test

I am writing a script to download the XML file from the URL given in the git readme file.

In [18]:
import json
import time
import requests
import numpy as np
import pandas as pd
from bs4 import BeautifulSoup

Here I upload the data raw from the website provided

In [19]:
url = "http://syndication.enterprise.websiteidx.com/feeds/BoojCodeTest.xml"

payload = "{}"
response = requests.request("GET", url, data=payload)

print(response.text)

<?xml version='1.0' encoding='UTF-8'?>
<Listings>

  <Listing>
    <Location>
      <StreetAddress>0 Castro Peak Mountainway</StreetAddress>
      <UnitNumber/>
      <City>Malibu</City>
      <State>CA</State>
      <Zip>90265</Zip>
      <ParcelID/>
      <Lat>34.087528</Lat>
      <Long>-118.804301</Long>
      <County/>
      <StreetIntersection/>
      <DisplayAddress>Yes</DisplayAddress>
    </Location>
    <ListingDetails>
      <Status>Active</Status>
      <Price>535000.00</Price>
      <ListingUrl>http://www.thepartnerstrust.com/property/42921875/syn/43/</ListingUrl>
      <MlsId>14799273</MlsId>
      <MlsName>CLAW</MlsName>
      <ProviderListingId>42921875</ProviderListingId>
      <DateListed>2014-10-03 00:00:00</DateListed>
      <VirtualTourUrl><![CDATA[http://www.thepartnerstrust.com/property/42921875/syn/43/]]></VirtualTourUrl>
      <ListingEmail>zillow-41@leadrelay.com</ListingEmail>
      <AlwaysEmailAgent>0</AlwaysEmailAgent>
      <ShortSale/>
      <REO/>
    </

As we can see, it's in XML format so I load in Beautiful Soup to my libraries above to clean it up a bit

In [20]:
soup = BeautifulSoup(response.text, 'lxml')

In [21]:
soup

<?xml version='1.0' encoding='UTF-8'?><html><body><listings>
<listing>
<location>
<streetaddress>0 Castro Peak Mountainway</streetaddress>
<unitnumber></unitnumber>
<city>Malibu</city>
<state>CA</state>
<zip>90265</zip>
<parcelid></parcelid>
<lat>34.087528</lat>
<long>-118.804301</long>
<county></county>
<streetintersection></streetintersection>
<displayaddress>Yes</displayaddress>
</location>
<listingdetails>
<status>Active</status>
<price>535000.00</price>
<listingurl>http://www.thepartnerstrust.com/property/42921875/syn/43/</listingurl>
<mlsid>14799273</mlsid>
<mlsname>CLAW</mlsname>
<providerlistingid>42921875</providerlistingid>
<datelisted>2014-10-03 00:00:00</datelisted>
<virtualtoururl></virtualtoururl>
<listingemail>zillow-41@leadrelay.com</listingemail>
<alwaysemailagent>0</alwaysemailagent>
<shortsale></shortsale>
<reo></reo>
</listingdetails>
<rentaldetails>
<availability></availability>
<leaseterm></leaseterm>
<depositfees></depositfees>
<utilitiesincluded>
<water></water>

### Feature Selections

In [22]:
dates = [t.text for t in soup.find_all('datelisted')]
mlsid = [t.text for t in soup.find_all('mlsid')]
mlsname = [t.text for t in soup.find_all('mlsname')]
street = [t.text for t in soup.find_all('streetaddress')]
price = [t.text for t in soup.find_all('price')]
bedrooms = [t.text for t in soup.find_all('bedrooms')]
bathrooms = [t.text for t in soup.find_all('bathrooms')]
appliances = [t.text for t in soup.find_all('appliances')]
description = [t.text for t in soup.find_all('description')]
fullbath = [t.text for t in soup.find_all('fullbathrooms')]
halfbath = [t.text for t in soup.find_all('halfbathrooms')]
threequarter = [t.text for t in soup.find_all('threequarterbathrooms')]

I looked through a few of the first listings to get a feel for the data.  I noticed a lot of data was missing in some of the fields.  I decided to pull each requested feature, throw them into a Pandas and then clean it up from there.  I was a little confused with what qualifies a *room* or *bathrooms*.  I wasn't sure if you wanted all the different sizes of bathrooms so I included them into the Pandas just in case.  I never figured out logically how to ascertain the total amount of *rooms*.  I wasn't sure if you considered a basement to be a room or a sauna to be a room.

In [23]:
data = [dates, mlsid, mlsname, street, price, bedrooms, bathrooms, appliances, description, fullbath,
        halfbath, threequarter]

In [24]:
df = pd.DataFrame(data)

In [25]:
df = df.T

In [26]:
df.head()

0         1     2                           3          4   \
0  2014-10-03 00:00:00  14799273  CLAW   0 Castro Peak Mountainway  535000.00   
1  2014-10-17 00:00:00  14802845  CLAW  23410 Civic Center Way, C1  200000.00   
2  2015-03-03 00:00:00  15883387  CLAW            0 SADDLE PEAK RD   23500.00   
3  2015-03-18 00:00:00  15888095  CLAW  23410 Civic Center Way, C1   72500.00   
4  2015-11-18 00:00:00  15959941  CLAW     21310 PACIFIC COAST HWY  230000.00   

  5  6                                                7  8  9  10 11  
0  0                                                                  
1  0                                                                  
2  3     \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n     4        
3  5     \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n     4  1     
4  2                                       \nRangeOven\n     1

In [27]:
df.shape

(438, 12)

Now I have the raw data in a Pandas DF, I can easily clean up the rest.  I am unhappy that the entires before I converted were 219.  It appears through the conversion from XML to Pandas, I doubled my rows.  I'll be keeping an eye out on what happened there by doing further investigation.

In [28]:
df.columns

RangeIndex(start=0, stop=12, step=1)

In [29]:
df.columns = ['Date', 'MLSid', 'MLS Name', 'Street', 'Price', 'Bedrooms', 'Bathrooms', 
                   'Appliances', 'Description', 'Fullbath', 'Halfbath', 'Threequarter Bath']

In [30]:
df_work = df

In [31]:
df.head()

Date     MLSid MLS Name                      Street  \
0  2014-10-03 00:00:00  14799273     CLAW   0 Castro Peak Mountainway   
1  2014-10-17 00:00:00  14802845     CLAW  23410 Civic Center Way, C1   
2  2015-03-03 00:00:00  15883387     CLAW            0 SADDLE PEAK RD   
3  2015-03-18 00:00:00  15888095     CLAW  23410 Civic Center Way, C1   
4  2015-11-18 00:00:00  15959941     CLAW     21310 PACIFIC COAST HWY   

       Price Bedrooms Bathrooms  \
0  535000.00        0             
1  200000.00        0             
2   23500.00        3             
3   72500.00        5             
4  230000.00        2             

                                        Appliances Description Fullbath  \
0                                                                         
1                                                                         
2  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n                    4   
3  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n                    4   
4                                    \nRangeOven\n                    1   

  Halfbath Threequarter Bath  
0                             
1                             
2                             
3        1                    
4

### Now begins my EDA with my ```df_work``` dataframe

In [32]:
df_work.isnull().sum()

Date                 219
MLSid                219
MLS Name             219
Street                 0
Price                219
Bedrooms             219
Bathrooms            219
Appliances           219
Description            0
Fullbath             219
Halfbath             219
Threequarter Bath    219
dtype: int64

In [33]:
df_work.dtypes

Date                 object
MLSid                object
MLS Name             object
Street               object
Price                object
Bedrooms             object
Bathrooms            object
Appliances           object
Description          object
Fullbath             object
Halfbath             object
Threequarter Bath    object
dtype: object

It looks like all the features are ```object``` and need to be converted

In [34]:
df_work['Date'] = pd.to_datetime(df_work['Date'])

In [35]:
df_work['Price'] = df_work['Price'].astype(float)

In [36]:
df_work['Bedrooms'].unique()

array(['0', '3', '5', '2', '6', '4', '7', '1', '8', None], dtype=object)

I noticed that there was a string ```'None'``` in the *numeric* column ```Bedrooms```.  This needed to be converted to a zero so it would easily be changed to an integer for the whole feature.

In [37]:
df_work['Bedrooms'] = df_work['Bedrooms'].replace('None', '0')

I decided to personally going through each feature with integers to assess unique values and correct the formatting

In [38]:
df_work['Bathrooms'].unique()

array(['', None], dtype=object)

In [39]:
df_work['Bathrooms'] = df_work['Bathrooms'].replace('None', '0')
df_work['Bathrooms'] = df_work['Bathrooms'].replace('', '0')

In [40]:
df_work['Fullbath'].unique()

array(['', '4', '1', '3', '2', '7', '5', '8', '6', None], dtype=object)

In [41]:
df_work['Fullbath'] = df_work['Fullbath'].replace('None', '0')
df_work['Fullbath'] = df_work['Fullbath'].replace('', '0')

In [42]:
df_work['Halfbath'].unique()

array(['', '1', '2', '3', '99', None], dtype=object)

This was an incredibly amusing find.  how can there be a listing with ```'99'``` Half Bathrooms?

In [43]:
df_work['Halfbath'] = df_work['Halfbath'].replace('None', '0')
df_work['Halfbath'] = df_work['Halfbath'].replace('', '0')

In [44]:
df_work['Halfbath'].value_counts()

0     139
1      72
2       5
3       2
99      1
Name: Halfbath, dtype: int64

It seems there was only one instance of a home with 99 Half Bathrooms so I felt it was necessary to change that to zero.

In [45]:
#df_work['Halfbath'] = df_work['Halfbath'].replace('99', '0')

**_NOTE: I noticed that there was 1 address with 83 listings below.  This would account for that 1 address to have so many Half Bathrooms.  I decided to change the 0 back to 99 for the integrity of the data_**

In [46]:
df_work['Threequarter Bath'].unique()

array(['', '1', '2', '3', '4', None], dtype=object)

In [47]:
df_work['Threequarter Bath'] = df_work['Threequarter Bath'].replace('None', '0')
df_work['Threequarter Bath'] = df_work['Threequarter Bath'].replace('', '0')

In [48]:
df_work.head()

Date     MLSid MLS Name                      Street     Price  \
0 2014-10-03  14799273     CLAW   0 Castro Peak Mountainway  535000.0   
1 2014-10-17  14802845     CLAW  23410 Civic Center Way, C1  200000.0   
2 2015-03-03  15883387     CLAW            0 SADDLE PEAK RD   23500.0   
3 2015-03-18  15888095     CLAW  23410 Civic Center Way, C1   72500.0   
4 2015-11-18  15959941     CLAW     21310 PACIFIC COAST HWY  230000.0   

  Bedrooms Bathrooms                                       Appliances  \
0        0         0                                                    
1        0         0                                                    
2        3         0  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n   
3        5         0  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n   
4        2         0                                    \nRangeOven\n   

  Description Fullbath Halfbath Threequarter Bath  
0                    0        0                 0  
1                    0        0                 0  
2                    4        0                 0  
3                    4        1                 0  
4                    1        0                 0

I realized that there were 219 *null* values that I decided to remove.  This I feel was the discrepancy I noticed earlier with the doubling of rows after converting to Pandas

In [49]:
df_work = df_work.dropna(axis=0, how = 'any')

Now I can convert all the necessary features into integers

In [50]:
df_work['Bedrooms'] = df_work['Bedrooms'].astype(int)
df_work['Bathrooms'] = df_work['Bathrooms'].astype(int)
df_work['Fullbath'] = df_work['Fullbath'].astype(int)
df_work['Halfbath'] = df_work['Halfbath'].astype(int)
df_work['Threequarter Bath'] = df_work['Threequarter Bath'].astype(int)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/p

In [51]:
df_work['Rooms'] = df_work['Bedrooms']+df_work['Bathrooms']+df_work['Fullbath']+df_work['Halfbath']+df_work['Threequarter Bath']

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [52]:
df_work.head()

Date     MLSid MLS Name                      Street     Price  \
0 2014-10-03  14799273     CLAW   0 Castro Peak Mountainway  535000.0   
1 2014-10-17  14802845     CLAW  23410 Civic Center Way, C1  200000.0   
2 2015-03-03  15883387     CLAW            0 SADDLE PEAK RD   23500.0   
3 2015-03-18  15888095     CLAW  23410 Civic Center Way, C1   72500.0   
4 2015-11-18  15959941     CLAW     21310 PACIFIC COAST HWY  230000.0   

   Bedrooms  Bathrooms                                       Appliances  \
0         0          0                                                    
1         0          0                                                    
2         3          0  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n   
3         5          0  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n   
4         2          0                                    \nRangeOven\n   

  Description  Fullbath  Halfbath  Threequarter Bath  Rooms  
0                     0         0                  0      0  
1                     0         0                  0      0  
2                     4         0                  0      7  
3                     4         1                  0     10  
4                     1         0                  0      3

In [53]:
df_work.dtypes

Date                 datetime64[ns]
MLSid                        object
MLS Name                     object
Street                       object
Price                       float64
Bedrooms                      int64
Bathrooms                     int64
Appliances                   object
Description                  object
Fullbath                      int64
Halfbath                      int64
Threequarter Bath             int64
Rooms                         int64
dtype: object

In [54]:
df_work['MLSid'].unique()

array(['14799273', '14802845', '15883387', '15888095', '15959941',
       '15965091', '16106762', '16109128', '16114818', '16115130',
       '16115640', '16118008', '16122648', '16125100', '16129206',
       '16130744', '16132084', '16132158', '16133142', '16134056',
       '16134704', '16134756', '16134906', '16135516', '16136820',
       '16137056', '16137086', '16141262', '16142180', '16142204',
       '16144050', '16145020', '16146358', '16146576', '16148546',
       '16150042', '16150280', '16150318', '16150758', '16151208',
       '16151674', '16153228', '16154748', '16154856', '16154966',
       '16155556', '16155592', '16156574', '16157052', '16157428',
       '16157766', '16157850', '16158240', '16158556', '16158874',
       '16159656', '16159808', '16160058', '16160314', '16161032',
       '16161068', '16161388', '16161666', '16162304', '16162424',
       '16162540', '16162570', '16162696', '16162826', '16163034',
       '16163198', '16163248', '16163266', '16163826', '161639

It looks like that not all the IDs are purely numeric.  At the very end, there seems to be a string element, hybrid of numbers and letters.

### Organizing Description

In [57]:
df_test = df_work

In [58]:
df_test.tail()

Date         MLSid       MLS Name  \
214 2016-11-18 07:45:06     316010702          ITECH   
215 2014-07-24 16:33:10        PT2979  partnerstrust   
216 2015-02-13 14:29:51        PT3446  partnerstrust   
217 2015-02-27 09:00:55        PT3481  partnerstrust   
218 2016-10-04 00:00:00  SB16712658MR          CRMLS   

                                 Street      Price  Bedrooms  Bathrooms  \
214                  1227 GRANVILLE AVE  1025000.0         4          0   
215   11726 San Vicente Blvd, Suite 350    50000.0         4          0   
216                     7462 CLINTON ST   999990.0         0          0   
217  9378 Wilshire Boulevard, Suite 200     3700.0         0          0   
218                   610 N Orlando AVE   779000.0         3          0   

           Appliances Description  Fullbath  Halfbath  Threequarter Bath  \
214  \nBuilt-In Gas\n                     1         0                  1   
215                                       4         0                  0   
216                                       0         0                  0   
217                                       2         0                  0   
218     \nRangeOven\n                     2        99                  0   

     Rooms  
214      6  
215      8  
216      0  
217      2  
218    104

In [59]:
df_test['Description'] = df_test['Description'].replace('', '0')

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [60]:
df_test.head()

Date     MLSid MLS Name                      Street     Price  \
0 2014-10-03  14799273     CLAW   0 Castro Peak Mountainway  535000.0   
1 2014-10-17  14802845     CLAW  23410 Civic Center Way, C1  200000.0   
2 2015-03-03  15883387     CLAW            0 SADDLE PEAK RD   23500.0   
3 2015-03-18  15888095     CLAW  23410 Civic Center Way, C1   72500.0   
4 2015-11-18  15959941     CLAW     21310 PACIFIC COAST HWY  230000.0   

   Bedrooms  Bathrooms                                       Appliances  \
0         0          0                                                    
1         0          0                                                    
2         3          0  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n   
3         5          0  \nBuilt-Ins\nRange Hood\nMicrowave\nRangeOven\n   
4         2          0                                    \nRangeOven\n   

  Description  Fullbath  Halfbath  Threequarter Bath  Rooms  
0           0         0         0                  0      0  
1           0         0         0                  0      0  
2           0         4         0                  0      7  
3           0         4         1                  0     10  
4           0         1         0                  0      3

Now that I was able to replace the non-values in the descriptions, or *blanks*, I was able to create a new data frame with just descriptions which were only 3.  I believe this has narrowed down the selections, however there are no accompanying data except ```Street``` address.  I feel like my initial steps of converting from XML to Pandas, I lost something

In [61]:
df_description = df_test[df_test['Description'] != '0']

In [62]:
df_description

Empty DataFrame
Columns: [Date, MLSid, MLS Name, Street, Price, Bedrooms, Bathrooms, Appliances, Description, Fullbath, Halfbath, Threequarter Bath, Rooms]
Index: []

In [63]:
df_description.to_csv('Description-only.csv')

### Organizing Date

In [64]:
df_test

Date         MLSid       MLS Name  \
0   2014-10-03 00:00:00      14799273           CLAW   
1   2014-10-17 00:00:00      14802845           CLAW   
2   2015-03-03 00:00:00      15883387           CLAW   
3   2015-03-18 00:00:00      15888095           CLAW   
4   2015-11-18 00:00:00      15959941           CLAW   
5   2015-12-11 00:00:00      15965091           CLAW   
6   2016-03-16 00:00:00      16106762           CLAW   
7   2016-03-25 00:00:00      16109128           CLAW   
8   2016-04-12 00:00:00      16114818           CLAW   
9   2016-04-13 00:00:00      16115130           CLAW   
10  2016-04-14 00:00:00      16115640           CLAW   
11  2016-04-25 00:00:00      16118008           CLAW   
12  2016-05-06 00:00:00      16122648           CLAW   
13  2016-05-16 00:00:00      16125100           CLAW   
14  2016-05-26 00:00:00      16129206           CLAW   
15  2016-06-02 00:00:00      16130744           CLAW   
16  2016-06-05 00:00:00      16132084           CLAW   
17  2016-06-06 00:00:00      16132158           CLAW   
18  2016-07-15 00:00:00      16133142           CLAW   
19  2016-06-11 00:00:00      16134056           CLAW   
20  2016-06-14 00:00:00      16134704           CLAW   
21  2016-06-14 00:00:00      16134756           CLAW   
22  2016-06-16 00:00:00      16134906           CLAW   
23  2016-06-16 00:00:00      16135516           CLAW   
24  2016-07-06 00:00:00      16136820           CLAW   
25  2016-06-22 00:00:00      16137056           CLAW   
26  2016-06-24 00:00:00      16137086           CLAW   
27  2016-07-06 00:00:00      16141262           CLAW   
28  2016-07-11 00:00:00      16142180           CLAW   
29  2016-07-21 00:00:00      16142204           CLAW   
..                  ...           ...            ...   
189 2016-10-15 16:59:01     316009737          ITECH   
190 2016-10-17 00:00:00     316009746          ITECH   
191 2016-10-19 00:00:00     316009753          ITECH   
192 2016-10-18 00:00:00     316009802          ITECH   
193 2016-10-19 21:51:45     316009844          ITECH   
194 2016-10-21 00:00:00     316009913          ITECH   
195 2016-11-02 00:00:00     316009971          ITECH   
196 2016-10-25 00:00:00     316010002          ITECH   
197 2016-10-26 00:00:00     316010040          ITECH   
198 2016-10-27 12:33:34     316010077          ITECH   
199 2016-10-28 00:00:00     316010117          ITECH   
200 2016-11-01 00:00:00     316010138          ITECH   
201 2016-10-31 00:00:00     316010184          ITECH   
202 2016-11-02 11:55:26     316010241          ITECH   
203 2016-11-03 07:20:11     316010261          ITECH   
204 2016-11-03 00:00:00     316010267          ITECH   
205 2016-11-05 06:16:15     316010316          ITECH   
206 2016-11-07 00:00:00     316010376          ITECH   
207 2016-11-10 00:00:00     316010426          ITECH   
208 2016-11-09 00:00:00     316010451          ITECH   
209 2016-11-11 00:00:00     316010501          ITECH   
210 2016-11-13 00:00:00     316010528          ITECH   
211 2016-11-14 00:00:00     316010536          ITECH   
212 2016-11-18 00:00:00     316010634          ITECH   
213 2016-11-17 00:00:00     316010650          ITECH   
214 2016-11-18 07:45:06     316010702          ITECH   
215 2014-07-24 16:33:10        PT2979  partnerstrust   
216 2015-02-13 14:29:51        PT3446  partnerstrust   
217 2015-02-27 09:00:55        PT3481  partnerstrust   
218 2016-10-04 00:00:00  SB16712658MR          CRMLS   

                                 Street       Price  Bedrooms  Bathrooms  \
0             0 Castro Peak Mountainway    535000.0         0          0   
1            23410 Civic Center Way, C1    200000.0         0          0   
2                      0 SADDLE PEAK RD     23500.0         3          0   
3            23410 Civic Center Way, C1     72500.0         5          0   
4               21310 PACIFIC COAST HWY    230000.0         2          0   
5            23410 Civic Center Way, C1   2988000.0         0          0   
6             

Now, time to focus on organizing the year and getting only 2016 and putting them in descending order

In [65]:
df_test = df_test[(df_test['Date'].dt.year == 2016)]

In [66]:
df_test.sort_values(by='Date', ascending = False)

Date      MLSid MLS Name  \
214 2016-11-18 07:45:06  316010702    ITECH   
212 2016-11-18 00:00:00  316010634    ITECH   
156 2016-11-18 00:00:00   16181228     CLAW   
155 2016-11-18 00:00:00   16181224     CLAW   
213 2016-11-17 00:00:00  316010650    ITECH   
154 2016-11-17 00:00:00   16180298     CLAW   
153 2016-11-16 00:00:00   16180182     CLAW   
211 2016-11-14 00:00:00  316010536    ITECH   
152 2016-11-14 00:00:00   16179602     CLAW   
210 2016-11-13 00:00:00  316010528    ITECH   
151 2016-11-11 00:00:00   16179540     CLAW   
150 2016-11-11 00:00:00   16179532     CLAW   
142 2016-11-11 00:00:00   16178020     CLAW   
147 2016-11-11 00:00:00   16178966     CLAW   
145 2016-11-11 00:00:00   16178844     CLAW   
149 2016-11-11 00:00:00   16179426     CLAW   
209 2016-11-11 00:00:00  316010501    ITECH   
129 2016-11-10 00:00:00   16174844     CLAW   
207 2016-11-10 00:00:00  316010426    ITECH   
148 2016-11-10 00:00:00   16179108     CLAW   
208 2016-11-09 00:00:00  316010451    ITECH   
146 2016-11-09 00:00:00   16178870     CLAW   
144 2016-11-08 00:00:00   16178498     CLAW   
206 2016-11-07 00:00:00  316010376    ITECH   
143 2016-11-07 00:00:00   16178144     CLAW   
205 2016-11-05 06:16:15  316010316    ITECH   
136 2016-11-04 00:00:00   16177234     CLAW   
137 2016-11-04 00:00:00   16177260     CLAW   
138 2016-11-04 00:00:00   16177272     CLAW   
141 2016-11-04 00:00:00   16177590     CLAW   
..                  ...        ...      ...   
28  2016-07-11 00:00:00   16142180     CLAW   
27  2016-07-06 00:00:00   16141262     CLAW   
24  2016-07-06 00:00:00   16136820     CLAW   
166 2016-07-04 00:00:00  316006255    ITECH   
26  2016-06-24 00:00:00   16137086     CLAW   
163 2016-06-22 00:00:00  316005809    ITECH   
25  2016-06-22 00:00:00   16137056     CLAW   
164 2016-06-22 00:00:00  316005875    ITECH   
23  2016-06-16 00:00:00   16135516     CLAW   
22  2016-06-16 00:00:00   16134906     CLAW   
21  2016-06-14 00:00:00   16134756     CLAW   
20  2016-06-14 00:00:00   16134704     CLAW   
19  2016-06-11 00:00:00   16134056     CLAW   
17  2016-06-06 00:00:00   16132158     CLAW   
16  2016-06-05 00:00:00   16132084     CLAW   
15  2016-06-02 00:00:00   16130744     CLAW   
14  2016-05-26 00:00:00   16129206     CLAW   
13  2016-05-16 00:00:00   16125100     CLAW   
12  2016-05-06 00:00:00   16122648     CLAW   
162 2016-05-05 00:00:00  316004149    ITECH   
11  2016-04-25 00:00:00   16118008     CLAW   
10  2016-04-14 00:00:00   16115640     CLAW   
9   2016-04-13 00:00:00   16115130     CLAW   
8   2016-04-12 00:00:00   16114818     CLAW   
7   2016-03-25 00:00:00   16109128     CLAW   
6   2016-03-16 00:00:00   16106762     CLAW   
161 2016-02-04 00:00:00  316000525    ITECH   
159 2016-01-20 00:00:00   16970871     CLAW   
158 2016-01-13 00:00:00   16970717     CLAW   
157 2016-01-07 00:00:00   16968013     CLAW   

                                 Street       Price  Bedrooms  Bathrooms  \
214                  1227 GRANVILLE AVE   1025000.0         4          0   
212                   15630 WOODVALE RD    785000.0         2          0   
156                         928 19TH ST   7488000.0         4          0   
155  9378 Wilshire Boulevard, Suite 200    839000.0         2          0   
213   11726 San Vicente Blvd, Suite 350   1299000.0         4          0   
154                  1616 N LA BREA AVE   1125000.0         3          0   
153   11726 San Vicente Blvd, Suite 350   1875000.0         3          0   
211   11726 San Vicente Blvd, Suite 350   2600000.0         5          0   
152                      1310 NAPOLI DR   3986000.0         3          0   
210                         235 MAIN ST    569900.0         4          0   
151          23410 Civic Center Way, C1   1650000.0         0          0   
150                     11768 ELLICE ST   1100000.0         0          0   
142                       702 MARINE ST   1188000.0         2          0   
147   11726 San Vicente Blvd, Suite 350 

I wasn't sure if this *should* have been in descending or ascending order.  I thought it would make more sense with recent first.

### Organizing Appliances

In [67]:
df_test['Appliances']

6                    \nBuilt-Ins\nMicrowave\nRangeOven\n
7      \nBuilt-Ins\nMicrowave\nBuilt-In Gas\nCooktop ...
8                   \nBuilt-Ins\nRange Hood\nRangeOven\n
9                                                       
10                                                      
11                           \nBuilt-In BBQ\nRangeOven\n
12                                                      
13     \nBuilt-In BBQ\nBuilt-Ins\nMicrowave\nRangeOven\n
14                                                      
15                                                      
16                                                      
17                \nBuilt-In BBQ\nMicrowave\nRangeOven\n
18                                         \nRangeOven\n
19                                                      
20                                                      
21                                                      
22     \nRange Hood\nMicrowave\nCooktop - Gas\nOven-G...
23                  \nBuilt-Ins

In [300]:
df_test.loc[df_test['Appliances'].str.contains('\n'), :]

Date         MLSid MLS Name  \
6   2016-03-16 00:00:00      16106762     CLAW   
7   2016-03-25 00:00:00      16109128     CLAW   
8   2016-04-12 00:00:00      16114818     CLAW   
11  2016-04-25 00:00:00      16118008     CLAW   
13  2016-05-16 00:00:00      16125100     CLAW   
17  2016-06-06 00:00:00      16132158     CLAW   
18  2016-07-15 00:00:00      16133142     CLAW   
22  2016-06-16 00:00:00      16134906     CLAW   
23  2016-06-16 00:00:00      16135516     CLAW   
24  2016-07-06 00:00:00      16136820     CLAW   
25  2016-06-22 00:00:00      16137056     CLAW   
26  2016-06-24 00:00:00      16137086     CLAW   
27  2016-07-06 00:00:00      16141262     CLAW   
28  2016-07-11 00:00:00      16142180     CLAW   
29  2016-07-21 00:00:00      16142204     CLAW   
30  2016-07-18 00:00:00      16144050     CLAW   
34  2016-07-29 00:00:00      16148546     CLAW   
35  2016-08-05 00:00:00      16150042     CLAW   
37  2016-08-05 00:00:00      16150318     CLAW   
38  2016-08-05 00:00:00      16150758     CLAW   
39  2016-08-11 00:00:00      16151208     CLAW   
40  2016-08-10 00:00:00      16151674     CLAW   
41  2016-08-15 00:00:00      16153228     CLAW   
42  2016-08-22 00:00:00      16154748     CLAW   
44  2016-08-19 00:00:00      16154966     CLAW   
45  2016-08-22 00:00:00      16155556     CLAW   
46  2016-08-22 00:00:00      16155592     CLAW   
47  2016-08-26 00:00:00      16156574     CLAW   
48  2016-08-26 00:00:00      16157052     CLAW   
49  2016-08-29 00:00:00      16157428     CLAW   
..                  ...           ...      ...   
169 2016-08-03 00:00:00     316007323    ITECH   
170 2016-09-06 00:00:00     316007560    ITECH   
171 2016-08-15 11:31:13     316007701    ITECH   
172 2016-08-19 00:00:00     316007842    ITECH   
174 2016-09-06 00:00:00     316008372    ITECH   
175 2016-09-09 00:00:00     316008538    ITECH   
177 2016-09-28 00:00:00     316008990    ITECH   
178 2016-09-25 00:00:00     316009006    ITECH   
179 2016-09-26 00:00:00     316009078    ITECH   
180 2016-09-28 00:00:00     316009157    ITECH   
182 2016-10-03 00:00:00     316009342    ITECH   
184 2016-10-07 00:00:00     316009356    ITECH   
188 2016-10-14 00:00:00     316009693    ITECH   
190 2016-10-17 00:00:00     316009746    ITECH   
191 2016-10-19 00:00:00     316009753    ITECH   
192 2016-10-18 00:00:00     316009802    ITECH   
195 2016-11-02 00:00:00     316009971    ITECH   
196 2016-10-25 00:00:00     316010002    ITECH   
200 2016-11-01 00:00:00     316010138    ITECH   
202 2016-11-02 11:55:26     316010241    ITECH   
203 2016-11-03 07:20:11     316010261    ITECH   
205 2016-11-05 06:16:15     316010316    ITECH   
206 2016-11-07 00:00:00     316010376    ITECH   
207 2016-11-10 00:00:00     316010426    ITECH   
210 2016-11-13 00:00:00     316010528    ITECH   
211 2016-11-14 00:00:00     316010536    ITECH   
212 2016-11-18 00:00:00     316010634    ITECH   
213 2016-11-17 00:00:00     316010650    ITECH   
214 2016-11-18 07:45:06     316010702    ITECH   
218 2016-10-04 00:00:00  SB16712658MR    CRMLS   

                                 Street       Price  Bedrooms Bathrooms  \
6                       23826 MALIBU RD     25000.0         3         0   
7            23410 Civic Center Way, C1      6500.0         2         0   
8                           943 16th ST   5800000.0         3         0   
11           23410 Civic Center Way, C1   6995000.0         5         0   
13           23410 Civic Center Way, C1    150000.0         6         0   
17   9378 Wilshire Boulevard, Suite 200     27500.0         3         0   
18                      1912 KELTON AVE   1699000.0         3         0   
22                      28011 PAQUET PL   1749000.0         2         0   
23           23410 Civic Center Way, C1   2195000.0         3         0   
24                      6237 BONSALL DR  17500000.0         5         0   
25           23410 Civic Center Way, C1   2035000.0         2         0   
26                

In [78]:
df_test['Appliances'] = df_test['Appliances'].str.replace('\n', ' ')

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [79]:
df_test

Date         MLSid MLS Name  \
6   2016-03-16 00:00:00      16106762     CLAW   
7   2016-03-25 00:00:00      16109128     CLAW   
8   2016-04-12 00:00:00      16114818     CLAW   
9   2016-04-13 00:00:00      16115130     CLAW   
10  2016-04-14 00:00:00      16115640     CLAW   
11  2016-04-25 00:00:00      16118008     CLAW   
12  2016-05-06 00:00:00      16122648     CLAW   
13  2016-05-16 00:00:00      16125100     CLAW   
14  2016-05-26 00:00:00      16129206     CLAW   
15  2016-06-02 00:00:00      16130744     CLAW   
16  2016-06-05 00:00:00      16132084     CLAW   
17  2016-06-06 00:00:00      16132158     CLAW   
18  2016-07-15 00:00:00      16133142     CLAW   
19  2016-06-11 00:00:00      16134056     CLAW   
20  2016-06-14 00:00:00      16134704     CLAW   
21  2016-06-14 00:00:00      16134756     CLAW   
22  2016-06-16 00:00:00      16134906     CLAW   
23  2016-06-16 00:00:00      16135516     CLAW   
24  2016-07-06 00:00:00      16136820     CLAW   
25  2016-06-22 00:00:00      16137056     CLAW   
26  2016-06-24 00:00:00      16137086     CLAW   
27  2016-07-06 00:00:00      16141262     CLAW   
28  2016-07-11 00:00:00      16142180     CLAW   
29  2016-07-21 00:00:00      16142204     CLAW   
30  2016-07-18 00:00:00      16144050     CLAW   
31  2016-07-21 00:00:00      16145020     CLAW   
32  2016-07-22 00:00:00      16146358     CLAW   
33  2016-07-22 00:00:00      16146576     CLAW   
34  2016-07-29 00:00:00      16148546     CLAW   
35  2016-08-05 00:00:00      16150042     CLAW   
..                  ...           ...      ...   
186 2016-10-07 00:00:00     316009501    ITECH   
187 2016-10-12 00:00:00     316009646    ITECH   
188 2016-10-14 00:00:00     316009693    ITECH   
189 2016-10-15 16:59:01     316009737    ITECH   
190 2016-10-17 00:00:00     316009746    ITECH   
191 2016-10-19 00:00:00     316009753    ITECH   
192 2016-10-18 00:00:00     316009802    ITECH   
193 2016-10-19 21:51:45     316009844    ITECH   
194 2016-10-21 00:00:00     316009913    ITECH   
195 2016-11-02 00:00:00     316009971    ITECH   
196 2016-10-25 00:00:00     316010002    ITECH   
197 2016-10-26 00:00:00     316010040    ITECH   
198 2016-10-27 12:33:34     316010077    ITECH   
199 2016-10-28 00:00:00     316010117    ITECH   
200 2016-11-01 00:00:00     316010138    ITECH   
201 2016-10-31 00:00:00     316010184    ITECH   
202 2016-11-02 11:55:26     316010241    ITECH   
203 2016-11-03 07:20:11     316010261    ITECH   
204 2016-11-03 00:00:00     316010267    ITECH   
205 2016-11-05 06:16:15     316010316    ITECH   
206 2016-11-07 00:00:00     316010376    ITECH   
207 2016-11-10 00:00:00     316010426    ITECH   
208 2016-11-09 00:00:00     316010451    ITECH   
209 2016-11-11 00:00:00     316010501    ITECH   
210 2016-11-13 00:00:00     316010528    ITECH   
211 2016-11-14 00:00:00     316010536    ITECH   
212 2016-11-18 00:00:00     316010634    ITECH   
213 2016-11-17 00:00:00     316010650    ITECH   
214 2016-11-18 07:45:06     316010702    ITECH   
218 2016-10-04 00:00:00  SB16712658MR    CRMLS   

                                 Street       Price  Bedrooms  Bathrooms  \
6                       23826 MALIBU RD     25000.0         3          0   
7            23410 Civic Center Way, C1      6500.0         2          0   
8                           943 16th ST   5800000.0         3          0   
9                      1333 Montana Ave      5499.0         3          0   
10                   27061 SEA VISTA DR    798000.0         0          0   
11           23410 Civic Center Way, C1   6995000.0         5          0   
12          27086 MALIBU COVE COLONY DR   6649000.0         3          0   
13           23410 Civic Center Way, C1    150000.0         6          0   
14                        36 BREEZE AVE      5975.0         4          0   
15                 1730 Ocean Park Blvd   2450000.0         0          0   
16                 31652 BROAD BEACH RD   2888000.0         0          0   
17   9

In [80]:
df_test.drop(columns = 'Test', inplace = True)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [81]:
df_test.head()

Date     MLSid MLS Name                      Street      Price  \
6  2016-03-16  16106762     CLAW             23826 MALIBU RD    25000.0   
7  2016-03-25  16109128     CLAW  23410 Civic Center Way, C1     6500.0   
8  2016-04-12  16114818     CLAW                 943 16th ST  5800000.0   
9  2016-04-13  16115130     CLAW            1333 Montana Ave     5499.0   
10 2016-04-14  16115640     CLAW          27061 SEA VISTA DR   798000.0   

    Bedrooms  Bathrooms                                         Appliances  \
6          3          0                     Built-Ins Microwave RangeOven    
7          2          0   Built-Ins Microwave Built-In Gas Cooktop - Ga...   
8          3          0                    Built-Ins Range Hood RangeOven    
9          3          0                                                      
10         0          0                                                      

   Description  Fullbath  Halfbath  Threequarter Bath  Rooms  
6            0         3         1                  0      7  
7            0         1         1                  0      4  
8            0         3         0                  0      6  
9            0         2         0                  0      5  
10           0         0         0                  0      0

In [82]:
df_test.to_csv('Final.csv')